## Maps

In [1]:
using PlotlyJS

Plotly javascript loaded.

In [2]:
function maps1()
    marker = attr(size=[20, 30, 15, 10],
                  color=[10, 20, 40, 50],
                  cmin=0,
                  cmax=50,
                  colorscale="Greens",
                  colorbar=attr(title="Some rate",
                                ticksuffix="%",
                                showticksuffix="last"),
                  line_color="black")
    trace = scattergeo(;mode="markers", locations=["FRA", "DEU", "RUS", "ESP"],
                        marker=marker, name="Europe Data")
    layout = Layout(geo_scope="europe", geo_resolution=50, width=500, height=550,
                    margin=attr(l=0, r=0, t=10, b=0))
    plot(trace, layout)
end
maps1()

In [ ]:
function maps2()
    @eval using DataFrames

    # read Data into dataframe
    nm = tempname()
    url = "https://raw.githubusercontent.com/plotly/datasets/master/2014_us_cities.csv"
    download(url, nm)
    df = readtable(nm)
    rm(nm)

    trace = scattergeo(;locationmode="USA-states",
                        lat=df[:lat],
                        lon=df[:lon],
                        hoverinfo="text",
                        text=[string(x[:name], " pop: ", x[:pop]) for x in eachrow(df)],
                        marker_size=df[:pop]/50_000,
                        marker_line_color="black", marker_line_width=2)
    geo = attr(scope="usa",
               projection_type="albers usa",
               showland=true,
               landcolor="rgb(217, 217, 217)",
               subunitwidth=1,
               countrywidth=1,
               subunitcolor="rgb(255,255,255)",
               countrycolor="rgb(255,255,255)")

    layout = Layout(;title="2014 US City Populations", showlegend=false, geo=geo)
    plot(trace, layout)
end
maps2()

## line/scatter

In [ ]:
function dumbell()
    # reference: https://plot.ly/r/dumbbell-plots/
    @eval using DataFrames

    # read Data into dataframe
    nm = tempname()
    url = "https://raw.githubusercontent.com/plotly/datasets/master/school_earnings.csv"
    download(url, nm)
    df = readtable(nm)
    rm(nm)

    # sort dataframe by male earnings
    df = sort(df, cols=[:Men], rev=false)

    men = scatter(;y=df[:School], x=df[:Men], mode="markers", name="Men",
                   marker=attr(color="blue", size=12))
    women = scatter(;y=df[:School], x=df[:Women], mode="markers", name="Women",
                     marker=attr(color="pink", size=12))

    lines = map(eachrow(df)) do r
        scatter(y=fill(r[:School], 2), x=[r[:Women], r[:Men]], mode="lines",
                name=r[:School], showlegend=false, line_color="gray")
    end

    data = Base.typed_vcat(GenericTrace, men, women, lines)
    layout = Layout(width=650, height=650, margin_l=100, yaxis_title="School",
                    xaxis_title="Annual Salary (thousands)",
                    title="Gender earnings disparity")

    plot(data, layout)
end
dumbell()

In [ ]:
function batman()
    # reference: https://github.com/alanedelman/18.337_2015/blob/master/Lecture01_0909/The%20Bat%20Curve.ipynb
    σ(x) = √(1-x.^2)
    el(x) = 3*σ(x/7)
    s(x) = 4.2 - 0.5*x - 2.0*σ(0.5*x-0.5)
    b(x) = σ(abs(2-x)-1) - x.^2/11 + 0.5x - 3
    c(x) = [1.7, 1.7, 2.6, 0.9]

    p(i, f; kwargs...) = scatter(;x=[-i; 0.0; i], y=[f(i); NaN; f(i)],
                                  marker_color="black", showlegend=false,
                                  kwargs...)
    traces = vcat(p(3:0.1:7, el; name="wings 1"),
                  p(4:0.1:7, t->-el(t); name="wings 2"),
                  p(1:0.1:3, s; name="Shoulders"),
                  p(0:0.1:4, b; name="Bottom"),
                  p([0, 0.5, 0.8, 1], c; name="head"))

    plot(traces, Layout(title="Batman"))
end
batman()

## Contour

In [ ]:
unction contour1()
    x = [-9, -6, -5 , -3, -1]
    y = [0, 1, 4, 5, 7]
    z = [10     10.625  12.5  15.625  20
         5.625  6.25    8.125 11.25   15.625
         2.5    3.125   5.    8.125   12.5
         0.625  1.25    3.125 6.25    10.625
         0      0.625   2.5   5.625   10]
    trace = contour(x=x, y=y, z=z)

    layout = Layout(title="Setting the X and Y Coordinates in a Contour Plot")
    plot(trace, layout)
end
contour1()

## 3d

In [ ]:
function random_line()
    n = 400
    rw() = cumsum(randn(n))
    trace1 = scatter3d(;x=rw(),y=rw(), z=rw(), mode="lines",
                        marker=attr(color="#1f77b4", size=12, symbol="circle",
                                    line=attr(color="rgb(0,0,0)", width=0)),
                        line=attr(color="#1f77b4", width=1))
    trace2 = scatter3d(;x=rw(),y=rw(), z=rw(), mode="lines",
                        marker=attr(color="#9467bd", size=12, symbol="circle",
                                    line=attr(color="rgb(0,0,0)", width=0)),
                        line=attr(color="rgb(44, 160, 44)", width=1))
    trace3 = scatter3d(;x=rw(),y=rw(), z=rw(), mode="lines",
                        marker=attr(color="#bcbd22", size=12, symbol="circle",
                                    line=attr(color="rgb(0,0,0)", width=0)),
                        line=attr(color="#bcbd22", width=1))
    layout = Layout(autosize=false, width=500, height=500,
                    margin=attr(l=0, r=0, b=0, t=65))
    plot([trace1, trace2, trace3], layout)
end
random_line()

In [ ]:
function multiple_surface()
    z1 = [8.83 8.89 8.81 8.87 8.90 8.87
          8.89 8.94 8.85 8.94 8.96 8.92
          8.84 8.90 8.82 8.92 8.93 8.91
          8.79 8.85 8.79 8.90 8.94 8.92
          8.79 8.88 8.81 8.90 8.95 8.92
          8.80 8.82 8.78 8.91 8.94 8.92
          8.75 8.78 8.77 8.91 8.95 8.92
          8.80 8.80 8.77 8.91 8.95 8.94
          8.74 8.81 8.76 8.93 8.98 8.99
          8.89 8.99 8.92 9.10 9.13 9.11
          8.97 8.97 8.91 9.09 9.11 9.11
          9.04 9.08 9.05 9.25 9.28 9.27
          9.00 9.01 9.00 9.20 9.23 9.20
          8.99 8.99 8.98 9.18 9.20 9.19
          8.93 8.97 8.97 9.18 9.20 9.18]
    z2 = map(x->x+1, z1)
    z3 = map(x->x-1, z1)
    trace1 = surface(z=z1)
    trace2 = surface(z=z2, showscale=false, opacity=0.9)
    trace3 = surface(z=z3, showscale=false, opacity=0.9)
    plot([trace1, trace2, trace3])
end
multiple_surface()